# Ouverture du fichier de la simulation Meca3D sous SolidWorks

Le fichier `linearite.crb` est une exportation des données d'une simulation Meca3D donnant la position angulaire du bras par rapport au bâti en fonction de la position angulaire du moteur.

In [ ]:
fichier = open('linearite.crb', 'r')
# Lecture du fichier et mise sous forme de liste
lignes = fichier.readlines()
# Fermer le fichier
fichier.close()

# Création des variables

In [ ]:
ang_m = []
ang_b = []

# Importation les données une à une

In [ ]:
for ligne in lignes:
    # Mettre le bon séparateur décimal (remplace les virgules par des points)
    ligne = ligne.replace(',','.') # Précaution
    # Enlever le retour chariot en fin de ligne
    # Séparer des données repéré par un point virgule
    donnees = ligne.rstrip('\n\r').split(" ")
    # Créer de la liste des points
    if len(donnees) == 2:
        ang_m.append(float(donnees[0]))
        ang_b.append(float(donnees[1]))

# Affichage des données avec une régression linéaire

In [ ]:
from matplotlib.pyplot import figure, plot, xlabel, ylabel, text, show
from scipy.stats import linregress

def afficherCourbe(x, y, message=''):
    # Afficher la courbe
    figure(dpi=150)
    plot(x,y)
    xlabel("Position angulaire du rotor du moteur \n"+"par rapport au stator du moteur \n"+"en degré")
    ylabel("Position angulaire du bras \n"+"par rapport à la chaise \n"+"en degré")

    # Faire la regression linéaire
    a, b, r, p, std_err = linregress(x,y)

    # Afficher le résultat
    x2 = [x[0], x[-1]]
    y2 = [a*x[0] + b, a*x[-1] + b]
    plot(x2,y2)

    show()

    texte = "L'équation de la droite est :\n"
    if b >= 0:
        texte += "y = "+format(a,'.3e')+" * x +"+format(b,'.2e')+"\n"
    else:
        texte += "y = "+format(a,'.3e')+" * x "+format(b,'.2e')+"\n"
    texte += "avec un coefficient de regression r² = "+format(r**2,'.3e')+"\n"
    texte += 'entre '+str(y[0])+' degrés et '+str(y[-1])+' degrés \n'
    texte += 'centré sur '+str((y[0]+y[-1])/2)+'  degrés\n'

    texte += message

    print(texte)

In [ ]:
afficherCourbe(ang_m,ang_b)

# Linéarisation à un point de fonctionnement choisi

In [ ]:
test = True
while test:
    try :
        valeur = float(input("Saisir un nombre entre "+str(min(ang_b))+"  et "+str(max(ang_b))+" : "))
        test = not (min(ang_b) <= valeur <= max(ang_b))
    except :
        print("Vous n'avez pas saisi un nombre.")
        test = True

i = 0
while i < len(ang_b)-2 and not (ang_b[i] <= valeur < ang_b[i+1]):
    i += 1

#print(i,' : ',ang_b[i],' <--> ',ang_b[i+1])

In [ ]:
iMin = i-1
if iMin < 0: iMin = 0
iMax = i+1
if iMax > len(ang_b)-1: iMax = len(ang_b)-1

# Faire la regression linéaire
a, b, r, p, std_err = linregress(ang_m[iMin:iMax+1],ang_b[iMin:iMax+1])

while r**2 > 0.999:
    iMin -= 1
    if iMin < 0: iMin = 0
    iMax += 1
    if iMax > len(ang_b)-1: iMax = len(ang_b)-1
    a, b, r, p, std_err = linregress(ang_m[iMin:iMax+1],ang_b[iMin:iMax+1])

    if iMin == 0 and iMax == len(ang_b)-1:
        r = 0

afficherCourbe(ang_m[iMin:iMax+1],ang_b[iMin:iMax+1])
